# Code for imperfect testing model based on BHM (2020) and user interface

### 1. What does this code do?

This code extends (and replicates Figure 6 in) Berger, Herkenhoff, Mongey (2020) - *An SEIR Infectious Disease Model with Testing and Conditional Quarantine" by introducing imperfect testing through <1 sensitivity and specificity.

To run the model for various parameter values, follow these instructions:
1. Scroll down to the indicated 'initialization cell' below, place cursor inside the cell, then press Ctrl+Enter.
    - This will compile some code and present the baseline calibration of the model
1. Click the button marked **[Run model]**
    - The code will take ~45-90s to run the model, and then display **"Done solving model"**
1. Click the button marked **[Show panel chart]** to display the figure
    - Accompanying the figure will be a slider for $\tau \in [0,0.05]$ (from zero to 10 times the value used in the paper), that can be moved to change the plot

Below we describe other parameters. To change other parameters refresh this page in your browser. Repeat the above and then before pressing **[Run model]**, choose alternative values for model parameters.

In case you want to see the raw contents of the cells, please choose 'Raw NB convert' for cell type. For executable code, change back to 'code'!

**To download the underlying code, please ...

### 2. What can I change?

- There are two sets of parameters that the user can change

#### 2.1 Preset parameters

The first set appear in Table 4 of the paper, and below are divided into three blocks
1. **Quarantine parameters**
    - $\xi^u\geq 0$ 
        - Baseline rate of quarantine that is used in the *Common quarantine* case
    - $\lambda^Q/\lambda\in[0,1]$ 
        - Effectiveness of quarantine. If equal to 1, then quarantine has no effect. We suggest in the paper that for Wuhan this is around 0.10, and use 0.50 as our baseline for counterfacutals
    - $A_{rel}\in[0,1]$ 
        - Relative productivity of asymptomatic quarantined individuals to asymptomatic non-quarantined individuals. 
             $$ Y_t = M_t^{A,NQ} + A_{rel}\times M_t^{A,Q} $$
        - If this is lower, then *Common quarantine* policy will lead to larger declines in output relative to *Targeted quarantine* policies.
1. **Disease parameters**
    - Number of initial infections in the US population
    - $\pi^D$ 
        - Rate at which *symptomatic* individuals die from the virus.
1. **Timing parameters**
    - Date of vaccine - In the paper we set this to 500 days
    - $1/\delta$
        - Gives the number of days that it takes, on average, to show symptoms once infected with the virus
    - $1/\omega^R$
        - Gives the number of days that it takes, on average, to recover from the virus
1. **Contagion parameters**
    - $R_0$
        - This is the baseline transmission rate. In the code $\rho^S$---the probability of infection conditional on meeting---is chosen to imply this level of $R_0$
   - $\rho^A/\rho^S$
        - This is measures the relative infectiousness of asymptomatic individuals. A meeting with a symptomatic individual results in infection with probability $\rho^S$. If $\rho^A/\rho^S=0.5$, then half as many meetings with asymptomatic individuals result in infection. In the paper we simply set this to 1.
    
#### 2.2 Policy parameters

The second set appear in Tables 5 and 6 of the paper, these are the very simply 'policy parameters' $\tau\geq 0$ and $\Delta\in[0,1]$ which represent the rate of daily testing and the slackening of quarantine measures that we use to construct our counterfactual.

- Chooses one of the two parameters to *Slide over*
- Set the range for the other parameter. 
    - When sliding over $\Delta$, the *upper value* is always 1, which represents no slackening of quarantine. User then chooses the *lower bound*.
    - When sliding over $\tau$, the *lower value* is always 0, which represents no testing. User then chooses the *upper bound*.
    - In both cases the grid of parameters that are considered is evenly spaced and has 10 points.
- Proceed as above: Click **[Run model]**, wait until it displays **"Done solving model"**, then click **[Show panel chart]**



#### 2.3 Optimization parameters

The third set of parameters sets decision variables for optimization. 

##### 2.3.1 Lockdown rate

These decision variables are used to optimize for lockdown profile. The variables are given as a vector of integers, where each integer creates a new decision variable, that adjusts the strength of lockdown starting from **simulation day given by the integer**. The optimization algorithm well then search for best values for lockdown rates for these days.

In [11]:
# Please give the lockdown policy making days for lockdown rate.
termination_step = 100
nsga2_pop_size = 14 # low for debugging
mutation_parameter = 8 # smaller value -> larger mutation


lockdown_policy_days = [15, 30, 60, 90, 120, 150, 200]
lockdown_policy_lower_limits = [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
#lockdown_policy_upper_limits = [0.005, 0.005, 0.005, 0.005, 0.005, 0.005, 0.005]
lockdown_policy_upper_limits = [0.001, 0.001, 0.001, 0.001, 0.001, 0.001, 0.001]


In [12]:
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# INSTRUCTIONS: Click to place cursor in this box, and then press Ctrl+Enter
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~


from IPython.display import Javascript
Javascript("Jupyter.notebook.execute_cells([5,7])")

<IPython.core.display.Javascript object>

In [13]:
from model_code import *
from jupyterWidgets import *

import numpy as np
from pymoo.util.misc import stack
from pymoo.model.problem import Problem
from pymoo.algorithms.nsga2 import NSGA2
from pymoo.factory import get_sampling, get_crossover, get_mutation
from pymoo.factory import get_termination
from pymoo.optimize import minimize
from pymoo.visualization.scatter import Scatter
from policy_epidemic_model_code import *
import matplotlib.pyplot as plt
from pymoo.performance_indicator.hv import Hypervolume


In [ ]:
# Toggle on/off the raw code
from IPython.display import HTML

HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to switch on/off the raw code"></form>''')

In [15]:
display(paramsPanel)

In [ ]:
# OPTIMIZATION


termination = get_termination("n_gen", termination_step) # Use small value for debugging - large for runs

corona_model = optimizable_corona_model(ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value, rel_ρ.value, δ_param.value, \
                 ωR_param.value, π_D.value, R_0.value, rel_λ.value, initial_infect.value)

class COVID_policy(Problem):

    def __init__(self, model, policy_control_days):

        self.model = model
        self.policy_control_days = policy_control_days

        super().__init__(n_var=len(policy_control_days),
                         n_obj=2,
                         n_constr=0,
                         xl=np.array(lockdown_policy_lower_limits),
                         xu=np.array(lockdown_policy_upper_limits))

    def _evaluate(self, x, out, *args, **kwargs):

        f1 = []
        f2 = []
        for j in range(len(x[:,1])):  # evaluate f1 and f2 for each individual
            # TODO:  implement calculation of f1, f2 for all individuals (represented by rows in x)

            policy = {} # this will hold the policy in format suitable for input to the epidemic model
            for (i, t) in enumerate(self.policy_control_days):
                policy[t] = x[j,i]

            Reported_D, Notinfected_D, Unreported_D, Infected_D, False_pos, False_neg, Recovered_D, Dead_D, Infected_T, Infected_not_Q, Infected_in_Q, Y_D, M_t, Y_total \
                = self.model.solve_case(self.model.optimization_no_test, policy)

            # objectives scaled to roughly same scale
            f1.append(Dead_D[-1]*self.model.pop/1000)
            f2.append(-Y_total/(14*365*self.model.T_years)) # algorithm minimizes, Y_total needs to be max'd -> negative
            
            #f1.append(Dead_D[-1])
            #f2.append(-Y_total) # algorithm minimizes, Y_total needs to be max'd -> negative


        out["F"] = np.column_stack([f1, f2])
        #out["G"] = np.column_stack([g1, g2])


problem = COVID_policy(corona_model, lockdown_policy_days)

algorithm = NSGA2(
    pop_size=nsga2_pop_size,
    n_offsprings=6,
    sampling=get_sampling("real_random"),
    crossover=get_crossover("real_sbx", prob=0.9, eta=15),
    mutation=get_mutation("real_pm", eta=mutation_parameter),
    eliminate_duplicates=True
)

print("Starting optimization: please wait...")
res = minimize(problem,
               algorithm,
               termination,
               seed=1,
               #pf=problem.pareto_front(use_cache=False),
               save_history=True,
               verbose=True)

with open('results/optimization_result.txt', 'w') as f:
    print(res.X, file=f)

with open('results/optimization_objectives.txt', 'w') as f:
    print(res.F, file=f)

print("Run complete and results saved.")

Starting optimization: please wait...
n_gen |  n_eval |  n_nds  | delta_ideal  | delta_nadir  |   delta_f   
    1 |      14 |       8 |            - |            - |            -
    2 |      20 |       9 |  0.00000E+00 |  0.00000E+00 |  0.014855156
    3 |      26 |      13 |  0.008293743 |  0.028213060 |  0.040551167
    4 |      32 |      14 |  0.00000E+00 |  0.00000E+00 |  0.016028531
    5 |      38 |      14 |  0.00000E+00 |  0.00000E+00 |  0.028758002
    6 |      44 |      14 |  0.00000E+00 |  0.00000E+00 |  0.008848688
    7 |      50 |      14 |  0.191639778 |  0.422968085 |  0.039849448
    8 |      56 |      14 |  0.00000E+00 |  0.00000E+00 |  0.003160282
    9 |      62 |      14 |  0.00000E+00 |  0.00000E+00 |  0.003602488
   10 |      68 |      14 |  0.00000E+00 |  0.00000E+00 |  0.019461171
   11 |      74 |      14 |  0.00000E+00 |  0.00000E+00 |  0.004572119
   12 |      80 |      14 |  0.00000E+00 |  0.00000E+00 |  0.012107927
   13 |      86 |      14 |  0.01595390

In [6]:
res.F

array([[ 4.83782516e-06, -7.94748941e+03],
       [ 7.78035066e-04, -9.89247262e+03],
       [ 2.44824714e-04, -9.33748638e+03],
       [ 8.92402432e-05, -8.83388553e+03],
       [ 5.64761927e-04, -9.72806412e+03],
       [ 3.59962908e-04, -9.49941247e+03],
       [ 1.46121161e-05, -8.33665246e+03],
       [ 3.57694309e-05, -8.52794437e+03],
       [ 1.23774124e-04, -9.07833063e+03],
       [ 1.69982070e-04, -9.20071584e+03],
       [ 4.74398269e-04, -9.64749959e+03],
       [ 6.74733770e-04, -9.81992305e+03],
       [ 7.20470478e-04, -9.85286576e+03],
       [ 4.03130351e-04, -9.57148808e+03]])

In [7]:
res.X

array([[6.12273436e-04, 9.94486215e-04, 9.05922962e-04, 9.90600630e-04,
        3.86570239e-04, 9.16227974e-04, 4.82746141e-04],
       [4.39346800e-05, 2.73985937e-05, 3.67144260e-07, 6.84134599e-05,
        1.11456869e-04, 9.12355578e-05, 1.31990666e-06],
       [4.44759394e-05, 3.32465777e-04, 7.44699101e-06, 6.94181426e-05,
        4.35497076e-04, 1.06553705e-04, 4.10846154e-05],
       [6.14174231e-04, 9.59377900e-05, 1.36723218e-04, 4.82573312e-05,
        3.83668211e-04, 7.34924698e-05, 4.72563437e-04],
       [4.39346800e-05, 1.51332283e-04, 1.54835442e-06, 6.78371241e-05,
        1.11456869e-04, 1.29552072e-04, 6.66283176e-06],
       [5.01549425e-05, 1.82467455e-04, 6.69800786e-06, 4.78371165e-05,
        3.98746059e-04, 8.04491794e-05, 4.59248957e-05],
       [3.99801133e-05, 9.96713797e-04, 1.32353063e-04, 8.29303263e-04,
        3.86570239e-04, 9.16227974e-04, 9.77967809e-07],
       [5.74459341e-04, 1.04703642e-04, 8.95025255e-04, 2.10493112e-04,
        1.05552324e-04, 6

In [8]:
lockdownpolicy_list = []
for j, x in enumerate(res.X):
    policy = {} # this will hold the policy in format suitable for input to the epidemic model
    for (i, t) in enumerate(lockdown_policy_days):
        policy[t] = x[i]

    lockdownpolicy_list.append(policy)


In [12]:
# Test implementation - doesn't use optimizer results
lockdownpolicy_list = []
for j, x in enumerate(restest):
    policy = {} # this will hold the policy in format suitable for input to the epidemic model
    for (i, t) in enumerate(lockdown_policy_days):
        policy[t] = x[i]

    lockdownpolicy_list.append(policy)


In [9]:
ff = generate_plots(Δ.value, τ.value, test_sens.value, test_spec.value, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value*14+3*14, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value, lockdownpolicy_list)

Creating a corona model with testing rate =  0.0  sensitivity =  0.95  and specificity =  0.95
starting experiment


In [10]:
ff

<p><center><span style="color:red">1. No testing - Common quarantine, Red [dotted]</span> , <span style="color:blue">2. Testing - Targeted quarantine: Blue [dashed]</span></center></p>

In [ ]:
# Design Space
plot = Scatter(title = "Design Space", axis_labels="x")
plot.add(res.X, s=30, facecolors='none', edgecolors='r')
#plot.add(ps, plot_type="line", color="black", alpha=0.7)
plot.do()
#plot.apply(lambda ax: ax.set_xlim(0.0, 5.0))
#plot.apply(lambda ax: ax.set_ylim(0.0, 0.2))
plot.show()

In [ ]:
# Objective Space
plot = Scatter(title = "Objective Space")
plot.add(res.F)
plot.do()
#plot.add(pf, plot_type="line", color="black", alpha=0.7)
plot.show()

In [ ]:
# create the performance indicator object with reference point (4,4)
metric = Hypervolume(ref_point=np.array([1, 1.0]))

# collect the population in each generation
pop_each_gen = [a.pop for a in res.history]

# receive the population in each generation
obj_and_feasible_each_gen = [pop[pop.get("feasible")[:,0]].get("F") for pop in pop_each_gen]

# calculate for each generation the HV metric
hv = [metric.calc(f) for f in obj_and_feasible_each_gen]

# function evaluations at each snapshot
n_evals = np.array([a.evaluator.n_eval for a in res.history])

# visualze the convergence curve
plt.plot(n_evals, hv, '-o')
plt.title("Convergence")
plt.xlabel("Function Evaluations")
plt.ylabel("Hypervolume")
plt.ylim([0.0,1.5])
plt.show()

In [ ]:
n_evals

In [ ]:
hv

In [ ]:
res.history[0].pop.get("X")

In [ ]:
display(run_box)

In [ ]:
τ_list = np.arange(0., τ_max.value + τ_step.value, τ_step.value)
Δ_list = np.arange(Δ_min.value, 1. + Δ_step.value, Δ_step.value)

if slide_var.value == 1:
    f = generate_plots(Δ.value, τ_list, test_sens.value, test_spec.value, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value*14+3*14, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value)
elif slide_var.value == 2:
    f = generate_plots(Δ_list, τ.value, test_sens.value, test_spec.value, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value*14+3*14, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value)
elif slide_var.value == 3:
    test_sens_list = np.arange(test_sens_min.value, test_sens_max.value + test_sens_step.value, test_sens_step.value)
    f = generate_plots(Δ.value, τ.value, test_sens_list, test_spec.value, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value*14+3*14, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value)
elif slide_var.value == 4:
    test_spec_list = np.arange(test_spec_min.value, test_spec_max.value + test_spec_step.value, test_spec_step.value)
    f = generate_plots(Δ.value, τ.value, test_sens.value, test_spec_list, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value*14+3*14, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value)
elif slide_var.value == 5:
    #lockdown_policy_list = 
    f = generate_plots(Δ.value, τ.value, test_sens.value, test_spec.value, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value*14+3*14, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value, lockdownpolicy_list=lockpolicy_list)
    
print("Done solving model.")

In [12]:
ff = generate_plots(Δ.value, τ.value, test_sens.value, test_spec.value, ξ_base.value, A_rel.value, r_AP.value, d_vaccine.value, \
                     rel_ρ.value, δ_param.value, ωR_param.value, π_D.value, \
                     R_0.value, rel_λ.value, initial_infect.value, slide_var.value, [{1000000: 0.5}])

Creating a corona model with testing rate =  0.0  sensitivity =  0.95  and specificity =  0.95
Solving model:  {'τA': 0.0, 'test_sens': 1.0, 'test_spec': 1.0, 'ξ_U': 0.0, 'ξ_P': 0.0, 'ξ_N': 0.0, 'ξ_R': 0.0, 'r_U': 0.98, 'r_P': 0.0, 'r_AP': 0.05, 'r_N': 0.98, 'r_R': 0.999, 'd_start_exp': 0.0, 'experiment': 'baseline_vaccine_tag'}
Solving model:  {'τA': 0.0, 'test_sens': 1.0, 'test_spec': 1.0, 'ξ_U': 0.0, 'ξ_P': 0.05071910291597881, 'ξ_N': 0.0, 'ξ_R': 0.0, 'r_U': 0.0, 'r_P': 0.0, 'r_AP': 0.003491091440327665, 'r_N': 0.0, 'r_R': 0.05071910291597881, 'experiment': 'baseline_vaccine_tag', 'd_start_exp': 238}
Solving model:  {'τA': 0.0, 'test_sens': 1.0, 'test_spec': 1.0, 'ξ_U': 0.0, 'ξ_P': 0.05071910291597881, 'ξ_N': 0.0, 'ξ_R': 0.0, 'r_U': 0.0, 'r_P': 0.0, 'r_AP': 0.003491091440327665, 'r_N': 0.0, 'r_R': 0.05071910291597881, 'experiment': 'baseline_vaccine_tag', 'd_start_exp': 238}
starting experiment


In [ ]:
f



In [ ]:
res.X

<p><center><span style="color:red">1. No testing - Common quarantine, Red [dotted]</span> , <span style="color:blue">2. Testing - Targeted quarantine: Blue [dashed]</span></center></p>